In [1]:
import pandas as pd
import numpy as np
import datetime as date
import matplotlib.pyplot as plt
import queue 
import math
import time
today=date.date.today()
print(today)
import pyodbc
from pyxlsb import open_workbook
connection = pyodbc.connect(
    driver='{iSeries Access ODBC Driver}',
    system='KNL400A',
    uid='JSKEATH',
    pwd='DUSTY35')

pd.options.display.max_rows = 50000
cursor = connection.cursor()

2021-08-30


In [23]:
#relevant fridays 
faketoday = date.datetime.now() + date.timedelta(hours = 132)
faketoday = faketoday.date()

friday0 = faketoday + date.timedelta(days = 4 - faketoday.weekday())           #this friday
friday_1 = faketoday + date.timedelta(days = -3 - faketoday.weekday())         #last friday
friday1 = faketoday + date.timedelta(days = 11 - faketoday.weekday())          #next friday
friday2 = faketoday + date.timedelta(days = 18 - faketoday.weekday())          #friday 2 weeks from now 
friday3 = faketoday + date.timedelta(days = 25 - faketoday.weekday())          #friday 3 weeks from now  
friday4 = faketoday + date.timedelta(days = 32 - faketoday.weekday())          #friday 4 weeks from now 

print("friday0:",friday0,"friday_1:",friday_1,"friday1:",friday1,"friday2:",friday2,"friday3:",friday3,"friday4:",friday4)
print("Weekly Overview being updated...")

friday0: 2021-08-20 friday_1: 2021-08-13 friday1: 2021-08-27 friday2: 2021-09-03 friday3: 2021-09-10 friday4: 2021-09-17
Weekly Overview being updated...


In [3]:
timer1 = time.perf_counter()
#import TinaPaint file, rename columns
lookup = pd.read_sql_query('select * from KNL400A.EGLIB.TINAPAINTX',connection)
lookup = lookup.rename(columns={"IBPRP4":"MPF","WADRQJ":"PDATE","WARCTO":"ORDER TYPE","WALITM":"PATTERN NUMBER","IMDSC1":"PATTERN DESCRIPTION","OPENQTY":"OPEN PATTERN QTY","WAUOM":"UOM","WARORN":"SALES ORDER","WADCTO":"SALES TYPE","WADOCO":"WORK ORDER","WALNID":"SALES LINE","WAUORG":"INITIAL WA QTY","WASRST":"WORK ORDER STATUS","WAWR01":"COLOR","WAWR07":"MIXING CENTER","WMCPIL":"COMPONENTS","WMUORG":"COMPONENT QTY","WAANSA01":"MANAGER NAME","IBANPL01":"PLANNER NAME","IBBUYR01":"BUYER NAME","IBCOTY":"COMPLETED QTY","IBSTKT01":"PATTERN TYPE","IBPRP401":"MPF DESCRIPTION","WMCPNT":"COMP TYPE","WMUKID":"UNIQUE ID","WMCPIA":"3RD COMP"})
lookup = lookup[['MPF','PDATE','PATTERN NUMBER','PATTERN DESCRIPTION','OPEN PATTERN QTY','SALES ORDER','WORK ORDER','SALES LINE','INITIAL WA QTY','WORK ORDER STATUS','COLOR','COMPONENTS','COMPONENT QTY','MANAGER NAME','PATTERN TYPE','MPF DESCRIPTION']]

#date manipulation of tinapaint date to friday, removal of 10/10/50s
lookup = lookup[lookup.PDATE != '10/10/50']
lookup.reset_index(drop=True,inplace=True)
lookup.loc[:,'WORK ORDER STATUS'] = (lookup['WORK ORDER STATUS']).astype('int32')
lookup.loc[:,'WORK ORDER'] = (lookup['WORK ORDER']).astype('int32')
lookup['PDATE'] = lookup['PDATE'].apply(lambda x: date.datetime.strptime(x,"%m/%d/%y"))
lookup['PDATE'] = lookup['PDATE'].apply(lambda x: x + date.timedelta(days = 4 - x.weekday()))
lookup['PDATE'] = lookup['PDATE'].apply(lambda x: x.date())
lookup['COMPONENTS']=lookup['COMPONENTS'].apply(lambda x: str(x))
lookup['COMPONENTS']=lookup['COMPONENTS'].apply(lambda x: x.strip())
lookup.loc[:,'COMPONENT QTY'] = (lookup['COMPONENT QTY']).astype('int32')

#truncation of data to smaller timeframe
monthago = friday0 - date.timedelta(30)
lookup = lookup[lookup.PDATE <= friday3]
lookup = lookup[lookup.PDATE > monthago]

#get rid of duplicate rows in tinapaint
lookup.drop_duplicates(subset=['WORK ORDER', 'COMPONENTS','COMPONENT QTY'],inplace=True)
lookup.reset_index(drop=True,inplace=True)

#import and merge MPF key to dataframe to add areas
mpfkey = pd.read_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\MPFareas.xlsx', usecols = "A,B")
##mpfkey = pd.read_excel('T:\share\Thomas\MPFareas.xlsx', usecols = "A,B")
lookup['MPF'] = lookup['MPF'].astype(str)
lookup = pd.merge(lookup,mpfkey,how = "left",on = "MPF")
lookup.COLOR.replace('    ',"N/A",inplace = True)
lookup['COLOR'] = lookup['COLOR'].apply(lambda x: x.strip())

#import and merge routing assembly times to dataframe; unique to each WA 
routingkey = pd.read_sql_query('select * from KNL400A.JDEQUERY.SEATMONJDX',connection)
routingkey = routingkey[['SDPPDJ','SDRORN','SDLITM','SDDSC1','SDUORG','WLRUNL','WLDSC1','WLMCU']]
routingkey['SDRORN'] = routingkey['SDRORN'].apply(lambda x: x.strip())
routingkey['SDLITM'] = routingkey['SDLITM'].apply(lambda x: x.strip())
routingkey['WLMCU'] = routingkey['WLMCU'].apply(lambda x: x.strip())
routingkey = routingkey[~routingkey.WLMCU.isin(['E62347','GAP000','E62338','E80125','E81144','E81149','E80138','E81162','E81177','E81903','E81148','E81153'])]
routingkey = routingkey.groupby(['SDPPDJ','SDRORN','SDLITM','WLMCU'],as_index=False).agg({'WLRUNL': 'sum'})
routingkey = routingkey.groupby(['SDPPDJ','SDRORN','SDLITM'],as_index=False).agg({'WLRUNL': 'sum'})
routingkey['SDPPDJ'] = routingkey['SDPPDJ'].apply(lambda x: date.datetime.strptime(x,"%m/%d/%y"))
routingkey['SDPPDJ'] = routingkey['SDPPDJ'].apply(lambda x: x.date())
routingkey = routingkey.sort_values(by=['SDPPDJ'])
routingkey = routingkey.rename(columns={"SDPPDJ":"DATE","SDRORN":"WORK ORDER","SDLITM":"PATTERN NUMBER","SDDSC1":"PATTERN DESCRIPTION","SDUORG":"INITIAL WA QTY","WLRUNL":"Hours Work","WLDSC1":"ACTION DESCRIPTION","WLMCU":"WORKING CENTER"})
routingkey.reset_index(drop=True,inplace=True)
routingkey['PATTERN NUMBER'] = routingkey['PATTERN NUMBER'].apply(lambda x: str(x))
routingkey['WORK ORDER'] = routingkey['WORK ORDER'].apply(lambda x: str(int(x)))
lookup['PATTERN NUMBER'] = lookup['PATTERN NUMBER'].apply(lambda x: x.strip())
lookup['WORK ORDER'] = lookup['WORK ORDER'].apply(lambda x: str(int(x)))
lookup = lookup.sort_values(by=['WORK ORDER'])
lookup=pd.merge(lookup,routingkey, how="left",on=['WORK ORDER','PATTERN NUMBER'])


#for WAs not shown in routingkey, take converted tinapaint date and manually compute routings using area averages
lookup['DATE'].fillna(lookup['PDATE'], inplace=True)
lookup.drop(columns=['PDATE'],inplace=True)

gl = lookup[lookup['AREA'] == 'Glass']
lg = lookup[lookup['AREA'] == 'Legs']
pp = lookup[lookup['AREA'] == 'Paint/Pack']
ro = lookup[lookup['AREA'] == 'Rockwell']
s5 = lookup[lookup['AREA'] == 'Station 50']
sy = lookup[lookup['AREA'] == 'Sys Assy']
ta = lookup[lookup['AREA'] == 'Tables']
gl['delete1'] = gl['INITIAL WA QTY']* 0.035
gl = gl[['WORK ORDER','delete1']]
lg['delete1'] = lg['INITIAL WA QTY']* 0.02
lg = lg[['WORK ORDER','delete1']]
pp['delete1'] = pp['INITIAL WA QTY']* 0.004
pp = pp[['WORK ORDER','delete1']]
ro['delete1'] = ro['INITIAL WA QTY']* 0.025
ro = ro[['WORK ORDER','delete1']]
s5['delete1'] = s5['INITIAL WA QTY']* 0.014
s5 = s5[['WORK ORDER','delete1']]
sy['delete1'] = sy['INITIAL WA QTY']* 0.054
sy = sy[['WORK ORDER','delete1']]
ta['delete1'] = ta['INITIAL WA QTY']* 0.04
ta = ta[['WORK ORDER','delete1']]

gl.drop_duplicates(inplace=True)
lg.drop_duplicates(inplace=True)
pp.drop_duplicates(inplace=True)
ro.drop_duplicates(inplace=True)
s5.drop_duplicates(inplace=True)
sy.drop_duplicates(inplace=True)
ta.drop_duplicates(inplace=True)

lookup = pd.merge(lookup,gl, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)
lookup = pd.merge(lookup,lg, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)
lookup = pd.merge(lookup,pp, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)
lookup = pd.merge(lookup,ro, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)
lookup = pd.merge(lookup,s5, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)
lookup = pd.merge(lookup,sy, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)
lookup = pd.merge(lookup,ta, how="left",on=['WORK ORDER'])
lookup['Hours Work'].fillna(lookup['delete1'], inplace=True)
lookup.drop(columns = ['delete1'],inplace=True)

#import and merge Vendor key to dataframe 
vendkey=pd.read_sql_query('select * from KNL400A.JDEQUERY.JDSBOMSXX',connection)
vendkey = vendkey[['IBVEND','IBVEND01','WMCPIL']]
vendkey = vendkey.drop_duplicates()
vendkey = vendkey.sort_values(by=['IBVEND'])
vendkey = vendkey.drop_duplicates(subset='WMCPIL', keep="last")
vendkey = vendkey[['IBVEND01','WMCPIL']]
vendkey=vendkey.rename(columns={"IBVEND01":"Supplier","WMCPIL":"COMPONENTS"})
vendkey['COMPONENTS']=vendkey['COMPONENTS'].apply(lambda x: x.strip())
vendkey.reset_index(drop=True,inplace=True)

lookup=pd.merge(lookup,vendkey,how="left",on="COMPONENTS")
lookup['Supplier']=lookup['Supplier'].fillna('ERROR')
lookup.Supplier.replace('** NOT FOUND ','METAL SHOP',inplace=True)

#change sales color codes to in house color codes
lookup.COLOR.replace('111','E40',inplace=True)
lookup.COLOR.replace('112','EB8',inplace=True)
lookup.COLOR.replace('113','EDS',inplace=True)
lookup.COLOR.replace('114','EFS',inplace=True)
lookup.COLOR.replace('115','EL9',inplace=True)
lookup.COLOR.replace('116','EHS',inplace=True)
lookup.COLOR.replace('117','EJ9',inplace=True)
lookup.COLOR.replace('118','EKS',inplace=True)
lookup.COLOR.replace('119','EUS',inplace=True)
lookup.COLOR.replace('120S','120',inplace=True)
lookup.COLOR.replace('611','EMS',inplace=True)
lookup.COLOR.replace('612','EG2',inplace=True)
lookup.COLOR.replace('613','ERS',inplace=True)
lookup.COLOR.replace('130','E0S',inplace=True)
lookup.COLOR.replace('131','E1S',inplace=True)
lookup.COLOR.replace('111S','E40',inplace=True)
lookup.COLOR.replace('112S','EB8',inplace=True)
lookup.COLOR.replace('113S','EDS',inplace=True)
lookup.COLOR.replace('114S','EFS',inplace=True)
lookup.COLOR.replace('115S','EL9',inplace=True)
lookup.COLOR.replace('116S','EHS',inplace=True)
lookup.COLOR.replace('117S','EJ9',inplace=True)
lookup.COLOR.replace('118S','EKS',inplace=True)
lookup.COLOR.replace('119S','EUS',inplace=True)
lookup.COLOR.replace('611S','EMS',inplace=True)
lookup.COLOR.replace('612S','EG2',inplace=True)
lookup.COLOR.replace('613S','ERS',inplace=True)
lookup.COLOR.replace('130S','E0S',inplace=True)
lookup.COLOR.replace('131S','E1S',inplace=True)
lookup.COLOR.replace('111T','ET2',inplace=True)
lookup.COLOR.replace('112T','EB7',inplace=True)
lookup.COLOR.replace('113T','EDT',inplace=True)
lookup.COLOR.replace('114T','EFT',inplace=True)
lookup.COLOR.replace('115T','EZ5',inplace=True)
lookup.COLOR.replace('116T','EHT',inplace=True)
lookup.COLOR.replace('117T','EJ0',inplace=True)
lookup.COLOR.replace('118T','EKT',inplace=True)
lookup.COLOR.replace('119T','EUT',inplace=True)
lookup.COLOR.replace('611T','EMT',inplace=True)
lookup.COLOR.replace('612T','EK2',inplace=True)
lookup.COLOR.replace('613T','EK5',inplace=True)
lookup.COLOR.replace('130T','E0T',inplace=True)
lookup.COLOR.replace('131T','E1T',inplace=True)

lookup = lookup[['MPF','DATE','PATTERN NUMBER','PATTERN DESCRIPTION','OPEN PATTERN QTY','SALES ORDER','WORK ORDER','SALES LINE','INITIAL WA QTY','WORK ORDER STATUS','COLOR','COMPONENTS','COMPONENT QTY','MANAGER NAME','PATTERN TYPE','MPF DESCRIPTION','AREA','Hours Work','Supplier']]


timer2 = time.perf_counter()
print('load time:')
print(timer2 - timer1)

<ipython-input-3-ee17b4a14f31>:69: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gl['delete1'] = gl['INITIAL WA QTY']* 0.035
<ipython-input-3-ee17b4a14f31>:71: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  lg['delete1'] = lg['INITIAL WA QTY']* 0.02
<ipython-input-3-ee17b4a14f31>:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/sta

load time:
335.4742698


In [10]:
#add assembly staffing factors; must be > 0
#staffkey = pd.read_excel('T:\share\Thomas\AssemblyStaffing.xlsx', usecols = "A,B")
#lookupclean=pd.merge(lookupclean,staffkey,how="left",on="AREA")
#lookupclean['Hours Work'] = lookupclean['Hours Work'] / lookupclean['Staff Factor']

In [24]:
#allcomps: all orders, components, etc. for the week; 3 week view 
allcomps21 = lookup[lookup.DATE == friday2]

#lookupforweeks: orders grouped by WA on the pattern level; 3 week view
lookupforweek21 = allcomps21.drop_duplicates(subset=['WORK ORDER', 'PATTERN NUMBER'])
lookupforweek21 = lookupforweek21.sort_values(by=['Hours Work'])
lookupforweek21.reset_index(drop=True,inplace=True)

#status40s: orders grouped by WA, only status >=40 with hours aggregated 
status40_21 = lookupforweek21[lookupforweek21['WORK ORDER STATUS'] > 39] 
status40_21 = status40_21.sort_values(by=['Hours Work'])
status40_21.reset_index(drop=True,inplace=True)

MPF        DATE      PATTERN NUMBER             PATTERN DESCRIPTION  \
0     ECC  2021-09-03            DP1MBT48  48" DIVIDENDS MARKERBOARD TRAY   
1     ECC  2021-09-03            DP1MBT48  48" DIVIDENDS MARKERBOARD TRAY   
2     ECC  2021-09-03            DP1MBT48  48" DIVIDENDS MARKERBOARD TRAY   
3     ECD  2021-09-03         5276D40H02P  84.30" POWER POLE 42" PANEL      
4     ECC  2021-09-03           DP7PPSKIT  POWER POLE KIT FOR POST DP7      
5     EFL  2021-09-03              YHP1OF  HORSEPOWER FILLER PLATE OUTLET   
6     EHC  2021-09-03        QG9714802114  BRKT,GALL TO PNL,DPG 2 THK RH    
7     EHC  2021-09-03        QG9714803114  BRKT,GALL TO PNL,DPG 2 THK LH    
8     EHC  2021-09-03        QG9714802114  BRKT,GALL TO PNL,DPG 2 THK RH    
9     EHC  2021-09-03        QG9714803114  BRKT,GALL TO PNL,DPG 2 THK LH    
10    GAR  2021-09-03             ANTKIT3  KIT, ANTENNA 3                   
11    GAR  2021-09-03             ANTKIT3  KIT, ANTENNA 3                   
12    GAR  2021-09-03             ANTKIT3  KIT, ANTENNA 3                   
13    GAR  2021-09-03             ANTKIT3  KIT, ANTENNA 3                   
14    GAR  2021-09-03             ANTKIT3  KIT, ANTENNA 3                   
15    EMF  2021-09-03          3AF4048613  DUAL UTILITY TRAY SUPPORT        
16    GAR  2021-09-03             ANTKIT3  KIT, ANTENNA 3                   
17    EMF  2021-09-03          3AF4048613  DUAL UTILITY TRAY SUPPORT        
18    EHA  2021-09-03            69418111  COVER,RACEWAY END    MT1CE1      
19    ECC  2021-09-03            DP1MBT36  36" DIVIDENDS MARKERBOARD TRAY   
20    EDD  2021-09-03                YBIG  DESK ASSEMBLY GAGE,SET OF 5      
21    EDD  2021-09-03                YBIG  DESK ASSEMBLY GAGE,SET OF 5      
22    EMF  2021-09-03          3AB4027111  ADAPTOR,DESK TO CRED             
23    EDD  2021-09-03             UTPS112  POWER STRIP,SINGLE SIDED 12W     
24    EDD  2021-09-03             UTPS112  POWER STRIP,SINGLE SIDED 12W     
25    EDD  2021-09-03             UTPS112  POWER STRIP,SINGLE SIDED 12W     
26    EDD  2021-09-03             UTPS112  POWER STRIP,SINGLE SIDED 12W     
27    EDD  2021-09-03             UTPS112  POWER STRIP,SINGLE SIDED 12W     
28    EDD  2021-09-03             UTPS112  POWER STRIP,SINGLE SIDED 12W     
29    EDD  2021-09-03             UTPS112  POWER STRIP,SINGLE SIDED 12W     
30    EDD  2021-09-03             UTPS112  POWER STRIP,SINGLE SIDED 12W     
31    EDD  2021-09-03             UTPS112  POWER STRIP,SINGLE SIDED 12W     
32    ECD  2021-09-03        QH3655801111  WLDMT,BRACKET,PWR BEAM TO YFGP   
33    GAR  2021-09-03             ANTKIT3  KIT, ANTENNA 3                   
34    EC3  2021-09-03        3AB900102111  COVER,COLUMN DESK Y TABLE        
35    GAR  2021-09-03            ANTKIT13  KIT, ANTENNA 13                  
36    EMF  2021-09-03          3AF4003613  HOUSING COVER                    
37    GAR  2021-09-03             ANTKIT3  KIT, ANTENNA 3                   
38    GAR  2021-09-03             ANTKIT3  KIT, ANTENNA 3                   
39    GAR  2021-09-03             ANTKIT3  KIT, ANTENNA 3                   
40    GAR  2021-09-03             ANTKIT3  KIT, ANTENNA 3                   
41    EDD  2021-09-03                YBIG  DESK ASSEMBLY GAGE,SET OF 5      
42    GAR  2021-09-03             ANTKIT3  KIT, ANTENNA 3                   
43    EMF  2021-09-03        3AF401502613  CENTR BEAM TELESCOPE TABLE       
44    EUI  2021-09-03      6TD400520281CR  X-COL,28.5L,POLISH,CU PLATE      
45    EUI  2021-09-03      6TD400520281CR  X-COL,28.5L,POLISH,CU PLATE      
46    EMF  2021-09-03          3AB4027111  ADAPTOR,DESK TO CRED             
47    EMF  2021-09-03          3AB4026111  CRADLE,DESK TO PED  25 1/8       
48    EDD  2021-09-03         KR3AB405900  GLIDE ASSY,3/8-16 THD/FIXED HT   
49    EDD  2021-09-03         KR3AB405900  GLIDE ASSY,3/8-16 THD/FIXED HT   
50    ECC  2021-09-03            YR1TPS24  POWER STRIP FOR TELESCOPE        
51

In [25]:
#Hours of work per assembly area per color 
def mpf_assy(weeklookup):

    lookupmpf=weeklookup.pivot_table(values='Hours Work',index=['AREA'],columns='COLOR',aggfunc=np.sum)
    lookupmpf=lookupmpf.fillna(0)
    lookupmpf.mask((lookupmpf > 0) & (lookupmpf < 0.001), 0.001, inplace=True)
    pd.options.display.max_columns = 50
    #lookupmpf[lookupmpf.index == 'Glass'] = lookupmpf[lookupmpf.index == 'Glass'].div(glass_coeff)
    lookupmpf.loc['Color Totals']= lookupmpf.sum(numeric_only=True, axis=0)
    lookupmpf.loc[:,'Area Totals'] = lookupmpf.sum(numeric_only=True, axis=1)

    return lookupmpf

#lookupmpf.head(100)

In [26]:
#lookupmpf, but flipped along the diagonal 
def col_assy(weeklookup):

    lookupcol=weeklookup.pivot_table(values='Hours Work',index=['COLOR'],columns='AREA',aggfunc=np.sum)
    lookupcol=lookupcol.fillna(0)
    lookupcol.mask((lookupcol > 0) & (lookupcol < 0.001), 0.001, inplace=True)
    #lookupcol['Glass'] = lookupcol['Glass'].div(glass_coeff)
    lookupcol.loc['Area Totals']= lookupcol.sum(numeric_only=True, axis=0)
    lookupcol.loc[:,'Color Totals'] = lookupcol.sum(numeric_only=True, axis=1)

    return lookupcol

#pd.options.display.max_columns = 50
#lookupcol.head(100)

In [27]:
mpf21 = mpf_assy(lookupforweek21)
col21 = col_assy(lookupforweek21)

In [9]:
##mpfto_0 = pd.read_excel('T:\share\Thomas\mpftable1.xlsx')
mpfto_0 = pd.read_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\mpftable1.xlsx')
mpfto_0.set_index('AREA', inplace=True)
#mpfto_0.to_excel(r'T:\share\Thomas\mpftable0.xlsx')
mpfto_0.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\mpftable0.xlsx')
##mpfto_1 = pd.read_excel('T:\share\Thomas\mpftable2.xlsx')
mpfto_1 = pd.read_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\mpftable2.xlsx')
mpfto_1.set_index('AREA', inplace=True)
#mpfto_1.to_excel(r'T:\share\Thomas\mpftable1.xlsx')
mpfto_1.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\mpftable1.xlsx')

##colto_0 = pd.read_excel('T:\share\Thomas\coltable1.xlsx')
colto_0 = pd.read_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\coltable1.xlsx')
colto_0.set_index('COLOR', inplace=True)
#colto_0.to_excel(r'T:\share\Thomas\coltable0.xlsx')
colto_0.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\coltable0.xlsx')
##colto_1 = pd.read_excel('T:\share\Thomas\coltable2.xlsx')
colto_1 = pd.read_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\coltable2.xlsx')
colto_1.set_index('COLOR', inplace=True)
#colto_1.to_excel(r'T:\share\Thomas\coltable1.xlsx')
colto_1.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\coltable1.xlsx')
#ADD FOR COLLLL 

In [11]:
#mpf21.to_excel(r'T:\share\Thomas\mpftable2.xlsx')
mpf21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\mpftable2.xlsx')
#col21.to_excel(r'T:\share\Thomas\coltable2.xlsx')
col21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\coltable2.xlsx')

In [28]:
#find area with most work, find all colors with work in that area, then choose the color with largest total hours, repeat
def paint_schedule(lookupmpf,lookupcol):
    colors = []
    colcopy = lookupcol.drop('Area Totals')
    colcopy = colcopy.drop('Color Totals', axis=1)
    mpfcopy = lookupmpf.drop('Color Totals')
    mpfcopy = mpfcopy.drop('Area Totals', axis=1)
    colcopy = round(colcopy,3)
    mpfcopy = round(mpfcopy,3)
    
    n = range(len(lookupmpf.columns.tolist()) - 1)
    
    for i in n: 
        
        colcopy.loc['Area Totals']= colcopy.sum(numeric_only=True, axis=0)
        colcopy.loc[:,'Color Totals'] = colcopy.sum(numeric_only=True, axis=1)
        mpfcopy.loc['Color Totals']= mpfcopy.sum(numeric_only=True, axis=0)
        mpfcopy.loc[:,'Area Totals'] = mpfcopy.sum(numeric_only=True, axis=1)
        #print(colcopy)
        colcopy = round(colcopy,3)
        mpfcopy = round(mpfcopy,3)   
    
        colnum = len(colcopy.columns)
        vals = colcopy.iloc[-1][0:colnum-1].values
        maxval = round(max(vals),3)
        
        temp = mpfcopy.loc[mpfcopy['Area Totals'] == maxval]
        #print(maxval)

        temp1 = colcopy[temp.index[0]] 
        
        #print(temp1)

        temp1 = temp1[temp1.values == 0] 

        #print(temp1.index.values)
        colortotals = colcopy['Color Totals']
        
        #print(colortotals)
        colortotals = colortotals.drop(temp1.index.values)
        colortotals = colortotals.drop('Area Totals')
        #print(colortotals)
        colortotals = colortotals[colortotals.values == max(colortotals)]
        colors.append(str(colortotals.index.values[0]))

        #print(colors)

        colcopy = colcopy.drop(colortotals.index.values[0])
        colcopy = colcopy.drop('Area Totals')
        colcopy = colcopy.drop('Color Totals', axis=1)
        mpfcopy = mpfcopy.drop(colortotals.index.values[0], axis=1)
        mpfcopy = mpfcopy.drop('Color Totals')
        mpfcopy = mpfcopy.drop('Area Totals', axis=1)

        #print(mpfcopy)
    
    return colors

In [29]:
paint21 = paint_schedule(mpf21, col21)

In [14]:
##paintto_0 = pd.read_excel('T:\share\Thomas\paintsched1.xlsx')
paintto_0 = pd.read_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintsched1.xlsx')
paintto_0 = paintto_0.iloc[: , 1:]
#paintto_0.to_excel(r'T:\share\Thomas\paintsched0.xlsx')
paintto_0.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintsched0.xlsx')
##paintto_1 = pd.read_excel('T:\share\Thomas\paintsched2.xlsx')
paintto_1 = pd.read_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintsched2.xlsx')
paintto_1 = paintto_1.iloc[: , 1:]
#paintto_1.to_excel(r'T:\share\Thomas\paintsched1.xlsx')
paintto_1.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintsched1.xlsx')

In [15]:
paintframe21 = pd.DataFrame(paint21)
paintframe21 = paintframe21[paintframe21[0] != 'N/A']
paintframe21.reset_index()
#paintframe21.to_excel(r'T:\share\Thomas\paintsched2.xlsx')
paintframe21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\paintsched2.xlsx')

In [30]:
#filter out all components from the metal shop for MS scheduling
def create_lookupms(lookupforweek, paintlist):
    
    lookupforweekms = pd.DataFrame()
    
    for i in range(len(paintlist)):

        appendthis = lookupforweek[lookupforweek['COLOR'] == paintlist[i]]
        lookupforweekms = lookupforweekms.append(appendthis)
        lookupforweekms.reset_index(drop=True,inplace=True)

    lookupforweekms = lookupforweekms[lookupforweekms.Supplier == 'METAL SHOP']
    lookupforweekms.reset_index(drop=True,inplace=True)
    return lookupforweekms

In [31]:
lookupforweekms21 = create_lookupms(allcomps21, paint21)

In [32]:
#establish dataframe with metal shop routings for each component
routingkey1 = pd.read_sql_query('select * from KNL400A.JDEQUERY.ROUTSDLB',connection)
routingkey1 = routingkey1[['IRKITL','IRDSC1','IRRUNL']]
routingkey1['IRKITL'] = routingkey1['IRKITL'].apply(lambda x: x.strip())
routingkey1['IRRUNL'] = routingkey1['IRRUNL'].apply(lambda x: x/100)
routingkey1 = routingkey1.drop_duplicates(subset=['IRKITL','IRDSC1'])
routingkey1 = routingkey1.groupby(['IRKITL'],as_index=False).agg({'IRRUNL': 'sum'})
routingkey1 = routingkey1.rename(columns={"IRKITL":"COMPONENTS","IRDSC1":"ACTION DESCRIPTION","IRRUNL":"Hours Prod"})
routingkey1.reset_index(drop=True,inplace=True)

lookupforweekms21=pd.merge(lookupforweekms21,routingkey1, how="left",on=['COMPONENTS'])
lookupforweekms21 = lookupforweekms21.sort_values(by=['Hours Prod'])
lookupforweekms21.reset_index(drop=True,inplace=True)

MPF        DATE      PATTERN NUMBER             PATTERN DESCRIPTION  \
0     EDC  2021-09-03         D2P1FVT2130  KIT,D2 WINDOW/FROST PWDR GLASS   
1     EDC  2021-09-03         D2P1GVT1424  D2 WINDOW KIT FULL TOP POS.      
2     EDC  2021-09-03         D2P1FVT2124  KIT,D2 WINDOW/FROST PWDR GLASS   
3     EDC  2021-09-03         D2P1GVT1424  D2 WINDOW KIT FULL TOP POS.      
4     EDC  2021-09-03         D2P1GVT1430  D2 WINDOW KIT FULL TOP POS.      
5     EDC  2021-09-03         D2P1GVT1430  D2 WINDOW KIT FULL TOP POS.      
6     EDC  2021-09-03         D2P1GVT1448  D2 WINDOW KIT FULL TOP POS.      
7     EDC  2021-09-03         D2P1GVT1448  D2 WINDOW KIT FULL TOP POS.      
8     EDC  2021-09-03         D2P1GVT1430  D2 WINDOW KIT FULL TOP POS.      
9     EDC  2021-09-03         D2P1GVT1430  D2 WINDOW KIT FULL TOP POS.      
10    EDC  2021-09-03         D2P1FVT2124  KIT,D2 WINDOW/FROST PWDR GLASS   
11    EDC  2021-09-03         D2P1FVT2124  KIT,D2 WINDOW/FROST PWDR GLASS   
12    EDC  2021-09-03         D2P1FVT2124  KIT,D2 WINDOW/FROST PWDR GLASS   
13    EDC  2021-09-03         D2P1GVT1424  D2 WINDOW KIT FULL TOP POS.      
14    EDC  2021-09-03         D2P1FVT2124  KIT,D2 WINDOW/FROST PWDR GLASS   
15    EDC  2021-09-03         D2P1FVT2148  KIT,D2 WINDOW/FROST PWDR GLASS   
16    EDC  2021-09-03         D2P1FVT2142  KIT,D2 WINDOW/FROST PWDR GLASS   
17    EDC  2021-09-03         D2P1FVT2142  KIT,D2 WINDOW/FROST PWDR GLASS   
18    EDC  2021-09-03         D2P1FVT2130  KIT,D2 WINDOW/FROST PWDR GLASS   
19    EDC  2021-09-03         D2P1FVT2130  KIT,D2 WINDOW/FROST PWDR GLASS   
20    EDC  2021-09-03         D2P1FVT2124  KIT,D2 WINDOW/FROST PWDR GLASS   
21    EDC  2021-09-03         D2P1FVT2124  KIT,D2 WINDOW/FROST PWDR GLASS   
22    EDC  2021-09-03         D2P1FVT2142  KIT,D2 WINDOW/FROST PWDR GLASS   
23    EDC  2021-09-03         D2P1FVT2142  KIT,D2 WINDOW/FROST PWDR GLASS   
24    EDC  2021-09-03         D2P1FVT2136  KIT,D2 WINDOW/FROST PWDR GLASS   
25    EDC  2021-09-03         D2P1FVT2136  KIT,D2 WINDOW/FROST PWDR GLASS   
26    EDC  2021-09-03         D2P1FVT2124  KIT,D2 WINDOW/FROST PWDR GLASS   
27    EDC  2021-09-03         D2P1FVT2130  KIT,D2 WINDOW/FROST PWDR GLASS   
28    EDC  2021-09-03         D2P1GVT1442  D2 WINDOW KIT FULL TOP POS.      
29    EDC  2021-09-03         D2P1GVT1424  D2 WINDOW KIT FULL TOP POS.      
30    EDC  2021-09-03         D2P1GVT1436  D2 WINDOW KIT FULL TOP POS.      
31    EDC  2021-09-03         D2P1GVT1436  D2 WINDOW KIT FULL TOP POS.      
32    EDC  2021-09-03         D2P1GVT1442  D2 WINDOW KIT FULL TOP POS.      
33    EDC  2021-09-03         D2P1GVT1436  D2 WINDOW KIT FULL TOP POS.      
34    EDC  2021-09-03         D2P1GVT1424  D2 WINDOW KIT FULL TOP POS.      
35    EDC  2021-09-03         D2P1GVT1424  D2 WINDOW KIT FULL TOP POS.      
36    EDC  2021-09-03         D2P1GVT1436  D2 WINDOW KIT FULL TOP POS.      
37    EDC  2021-09-03         D2P1FVT2148  KIT,D2 WINDOW/FROST PWDR GLASS   
38    EDC  2021-09-03         D2P1GVT1448  D2 WINDOW KIT FULL TOP POS.      
39    EDC  2021-09-03         D2P1GVT1448  D2 WINDOW KIT FULL TOP POS.      
40    EDC  2021-09-03         D2P1GVT1448  D2 WINDOW KIT FULL TOP POS.      
41    EDC  2021-09-03         D2P1GVT1424  D2 WINDOW KIT FULL TOP POS.      
42    EDC  2021-09-03         D2P1GVT1424  D2 WINDOW KIT FULL TOP POS.      
43    EDC  2021-09-03         D2P1GVT1448  D2 WINDOW KIT FULL TOP POS.      
44    EDB  2021-09-03         DP1AU1430VG  FRAMELESS ADD UP, GLASS          
45    EDB  2021-09-03         DP1AU1472VG  FRAMELESS ADD UP, GLASS          
46    EDB  2021-09-03         DP1AU1472VG  FRAMELESS ADD UP, GLASS          
47    EDB  2021-09-03         DP1AU1472VG  FRAMELESS ADD UP, GLASS          
48    EDB  2021-09-03         DP1AU1472VG  FRAMELESS ADD UP, GLASS          
49    EDB  2021-09-03         DP1AU1472VG  FRAMELESS ADD UP, GLASS          
50    EDB  2021-09-03         DP1AU1448VG  FRAMELESS ADD UP, GLASS          
51

In [33]:
#Number of MS components per color 
def comp_ms(lookupforweekms):

    lookupcomp = lookupforweekms.pivot_table(values='COMPONENT QTY',index=['COMPONENTS'],columns='COLOR',aggfunc=np.sum)
    lookupcomp=lookupcomp.fillna(0)

    lookupcomp.loc['Color Totals']= lookupcomp.sum(numeric_only=True, axis=0)
    lookupcomp.loc[:,'Component Totals'] = lookupcomp.sum(numeric_only=True, axis=1)

    pd.options.display.max_rows = 50000

    return lookupcomp

In [34]:
comp21 = comp_ms(lookupforweekms21)

non_ms21 = list(set(paint21) ^ set(comp21.columns.tolist()))
paint21 = [e for e in paint21 if e not in non_ms21]

In [35]:
#parsing through paintlist, find components with exclusive color runs, then mixed ones ; splits large component qtys
def shop_schedule(paintlist, lookupcomp):
    lookupcomp1 = lookupcomp
    comps = []
    amounts = []
    colors = [] 
    lookupcomp1 = lookupcomp1.drop('Color Totals')
    
    print('Truncated paintlist')
    
    for cur, nxt in zip(paintlist, paintlist[1:]):
        
        #if lookupcomp1['Component Totals'].sum() == 0:
                #break
            
        if lookupcomp1.empty == True:
            break;

        if cur in lookupcomp1.columns:
            lookupcomp1 = lookupcomp1.drop('Component Totals', axis=1)
            lookupcomp1.loc[:,'Component Totals'] = lookupcomp1.sum(numeric_only=True, axis=1)
            #print('Current Color')
            print(cur)
        
            #print(lookupcomp1)
            head = lookupcomp1.loc[lookupcomp1[cur] > 0]
            #print(head)
            head = head.loc[head[cur] == head['Component Totals']]
            
            while head.empty == False: 
                drop = head[cur].idxmax()
                top = head[cur].max()
                #comps.append([drop, 'All'])
                comps.append(drop)
                amounts.append(top)
                colors.append(cur)
                lookupcomp1 = lookupcomp1.drop(drop)
                head = head.drop(drop)
                #print(comps)
            
            #will hit if only multicolor components exist
            if head.empty == True: 
                head = lookupcomp1.loc[lookupcomp1[cur] > 0]
                next_run = head.loc[head[nxt] > 0]
                next_run = next_run[[cur,nxt,'Component Totals']]
                next_run.reset_index(level=0, inplace=True)
                next_run=pd.merge(next_run,routingkey1, how="left",on=['COMPONENTS'])
                next_run = next_run.set_index(['COMPONENTS'])
                next_run['Hours Prod'] = next_run['Hours Prod'] * (next_run['Component Totals'] - next_run[cur] - next_run[nxt])
                next_run = next_run.sort_values(by=['Hours Prod'])
                next_run['cur%'] = next_run[cur] / next_run['Component Totals']
                more_run = head.loc[head[nxt] == 0]
                more_run = more_run[[cur,'Component Totals']]
                more_run.reset_index(level=0, inplace=True)
                more_run=pd.merge(more_run,routingkey1, how="left",on=['COMPONENTS'])
                more_run = more_run.set_index(['COMPONENTS'])
                more_run['Hours Prod'] = more_run['Hours Prod'] * (more_run['Component Totals'] - more_run[cur])
                more_run = more_run.sort_values(by=['Hours Prod'])
                more_run['cur%'] = more_run[cur] / more_run['Component Totals']
                split_next = next_run.loc[next_run['Hours Prod'] > 1]
                split_more = more_run.loc[more_run['Hours Prod'] > 1]
                next_run = next_run.drop(split_next.index)
                more_run = more_run.drop(split_more.index)
                
                
                while next_run.empty == False:   
                    drop = next_run['cur%'].idxmax()
                    top = next_run[cur][next_run['cur%'].idxmax()]
                    #comps.append([drop, 'ALL'])
                    comps.append(drop)
                    amounts.append(top)
                    colors.append(cur)
                    
                    lookupcomp1 = lookupcomp1.drop(drop)
                    head = head.drop(drop)
                    next_run = next_run.drop(drop)
                    
                while split_next.empty == False:
                    drop = split_next['cur%'].idxmax()
                    row = split_next[split_next.index == drop]
                    number1 = row[cur]
                    number2 = row[nxt]
                    #comps.append([drop, int(number1), cur])
                    #comps.append([drop, int(number2), nxt])
                    comps.append(drop)
                    amounts.append(int(number1))
                    colors.append(cur)
                    comps.append(drop)
                    amounts.append(int(number2))
                    colors.append(nxt)
                    
                    
                    #print(comps)
                    headie = head[head.index == drop]
                    headie[cur] = headie[cur] - number1
                    headie[nxt] = headie[nxt] - number2
                    headie['Component Totals'] = headie['Component Totals'] - (number1 + number2)
                    head = head.drop(drop)      
                    head = pd.concat([head,headie])
                    lookupcomp1 = lookupcomp1.drop(drop)
                    lookupcomp1 = pd.concat([lookupcomp1,headie])
                    split_next = split_next.drop(drop)
                    
                while more_run.empty == False:                             
                    drop = more_run['cur%'].idxmax()
                    top = more_run[cur][more_run['cur%'].idxmax()]
                    #comps.append([drop, 'ALL'])
                    comps.append(drop)
                    amounts.append(top)
                    colors.append(cur)
                    
                    #print('morerun:')
                    #print(more_run)
                    #print(lookupcomp1)
                    lookupcomp1 = lookupcomp1.drop(drop)
                    head = head.drop(drop)
                    more_run = more_run.drop(drop)
                    
                while split_more.empty == False:
                    drop = split_more['cur%'].idxmax()
                    row = split_more[split_more.index == drop]
                    number1 = row[cur]
                    #comps.append([drop, int(number1), cur])
                    comps.append(drop)
                    amounts.append(int(number1))
                    colors.append(cur)
                    
                    #print(comps)
                    headie = head[head.index == drop]
                    headie[cur] = headie[cur] - number1
                    headie['Component Totals'] = headie['Component Totals'] - number1
                    head = head.drop(drop)      
                    head = pd.concat([head,headie])
                    lookupcomp1 = lookupcomp1.drop(drop)
                    lookupcomp1 = pd.concat([lookupcomp1,headie])
                    split_more = split_more.drop(drop)
                    
            #only multicolor
            if lookupcomp1[cur].sum() > 0:
                head = lookupcomp1.loc[lookupcomp1[cur] > 0]
                next_run = head.loc[head[nxt] > 0]
                #next_run = next_run.drop_duplicates()
                next_run = next_run[[cur,nxt,'Component Totals']]
                next_run.reset_index(level=0, inplace=True)
                next_run=pd.merge(next_run,routingkey1, how="left",on=['COMPONENTS'])
                next_run = next_run.set_index(['COMPONENTS'])
                next_run['Hours Prod'] = next_run['Hours Prod'] * (next_run['Component Totals'] - next_run[cur] - next_run[nxt])
                next_run = next_run.sort_values(by=['Hours Prod'])
                next_run['cur%'] = next_run[cur] / next_run['Component Totals']
                more_run = head.loc[head[nxt] == 0]
                more_run = more_run[[cur,'Component Totals']]
                more_run.reset_index(level=0, inplace=True)
                more_run=pd.merge(more_run,routingkey1, how="left",on=['COMPONENTS'])
                more_run = more_run.set_index(['COMPONENTS'])
                more_run['Hours Prod'] = more_run['Hours Prod'] * (more_run['Component Totals'] - more_run[cur])
                more_run = more_run.sort_values(by=['Hours Prod'])
                more_run['cur%'] = more_run[cur] / more_run['Component Totals']
                split_next = next_run.loc[next_run['Hours Prod'] > 1]
                split_more = more_run.loc[more_run['Hours Prod'] > 1]
                next_run = next_run.drop(split_next.index)
                more_run = more_run.drop(split_more.index)
                
                while next_run.empty == False:             
                    drop = next_run['cur%'].idxmax()
                    top = next_run[cur][next_run['cur%'].idxmax()]
                    #print(next_run)
                    #comps.append([drop, 'ALL'])
                    comps.append(drop)
                    amounts.append(top)
                    colors.append(cur)
                    
                    lookupcomp1 = lookupcomp1.drop(drop)
                    head = head.drop(drop)
                    next_run = next_run.drop(drop)
                
                while split_next.empty == False:
                    drop = split_next['cur%'].idxmax()
                    row = split_next[split_next.index == drop]
                    number1 = row[cur]
                    number2 = row[nxt]
                    #comps.append([drop, int(number1), cur])
                    #comps.append([drop, int(number2), nxt]) 
                    comps.append(drop)
                    amounts.append(int(number1))
                    colors.append(cur)
                    comps.append(drop)
                    amounts.append(int(number2))
                    colors.append(nxt)
                    
                    #print(comps)
                    headie = head[head.index == drop]
                    headie[cur] = headie[cur] - number1
                    headie[nxt] = headie[nxt] - number2
                    headie['Component Totals'] = headie['Component Totals'] - (number1 + number2)
                    head = head.drop(drop)      
                    head = pd.concat([head,headie])
                    lookupcomp1 = lookupcomp1.drop(drop)
                    lookupcomp1 = pd.concat([lookupcomp1,headie])
                    split_next = split_next.drop(drop)
                    
                while more_run.empty == False:                             
                    drop = more_run['cur%'].idxmax()
                    top = more_run[cur][more_run['cur%'].idxmax()]
                    #comps.append([drop, 'ALL'])
                    comps.append(drop)
                    amounts.append(top)
                    colors.append(cur)
                    
                    lookupcomp1 = lookupcomp1.drop(drop)
                    head = head.drop(drop)
                    more_run = more_run.drop(drop)
                    
                while split_more.empty == False:
                    drop = split_more['cur%'].idxmax()
                    row = split_more[split_more.index == drop]
                    number1 = row[cur]
                    #comps.append([drop, int(number1), cur])
                    comps.append(drop)
                    amounts.append(int(number1))
                    colors.append(cur)
                    
                    #print(comps)
                    headie = head[head.index == drop]
                    headie[cur] = headie[cur] - number1
                    headie['Component Totals'] = headie['Component Totals'] - number1
                    head = head.drop(drop)      
                    head = pd.concat([head,headie])
                    lookupcomp1 = lookupcomp1.drop(drop)
                    lookupcomp1 = pd.concat([lookupcomp1,headie])
                    split_more = split_more.drop(drop)
                    
            if lookupcomp1['Component Totals'].sum() == lookupcomp1[paintlist[-1]].sum():
                if lookupcomp1.empty == False:
                    print(paintlist[-1])
                    drop = lookupcomp1[paintlist[-1]].idxmax()
                    top = lookupcomp1[paintlist[-1]].max()
                    #comps.append([drop, 'ALL'])
                    comps.append(drop)
                    amounts.append(top)
                    colors.append(paintlist[-1])

                    lookupcomp1 = lookupcomp1.drop(drop)
    
    shopf1 = pd.DataFrame(comps)
    shopf2 = pd.DataFrame(amounts)
    shopf3 = pd.DataFrame(colors)
    shopframe = pd.concat([shopf1, shopf2, shopf3], axis = 1)
    
    return shopframe
    

In [40]:
##shopto_0 = pd.read_excel('T:\share\Thomas\MSsched1.xlsx')
shopto_0 = pd.read_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\MSsched1.xlsx')
shopto_0 = shopto_0.iloc[: , 1:]
#shopto_0.to_excel(r'T:\share\Thomas\MSsched0.xlsx')
shopto_0.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\MSsched0.xlsx')
##shopto_1 = pd.read_excel('T:\share\Thomas\MSsched2.xlsx')
shopto_1 = pd.read_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\MSsched2.xlsx')
shopto_1 = shopto_1.iloc[: , 1:]
#shopto_1.to_excel(r'T:\share\Thomas\MSsched1.xlsx')
shopto_1.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\MSsched1.xlsx')

In [41]:
#export MS schedules to excel files 
shop21 = shop_schedule(paint21, comp21)
shop21.columns = ['Components', 'Quantity', 'Color']
#shop21.to_excel('T:\share\Thomas\MSsched2.xlsx')
shop21.to_excel(r'\\knl4prd-efs01\Tableau\obot\PaintlineSched\MSsched2.xlsx')

Truncated paintlist
EKT
N/A
EZ5
ET2
E40
EGX
EG2

<ipython-input-35-fe785f86abcf>:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie[cur] = headie[cur] - number1
<ipython-input-35-fe785f86abcf>:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  headie['Component Totals'] = headie['Component Totals'] - number1
<ipython-input-35-fe785f86abcf>:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydat


EKS
EK5
EJ0
ERS
EFT
EL9
EDT
EJ9
E58
138
EB7
EFS
146
EHT
EMS
E1T
